In [17]:
import os
import pandas as pd
from datetime import datetime

In [18]:
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_tables_draft = os.path.join(path_root, 'draft', 'data', 'tables')
path_tables = os.path.join(path_root,'data', 'tables')

In [19]:
alphs = ['A', 'B']
now = datetime.now()

In [20]:
plan = pd.read_csv(os.path.join(path_tables_draft, 'plan.csv'))
plan = plan.drop(columns=[f'red_{alph}{i}' for alph in alphs for i in range(1,9)])
plan = plan.drop(columns=[f'yellow_{alph}{i}' for alph in alphs for i in range(1,9)])
plan['PLAN_NO'] = 1
plan['LAST_MDFCN_DT'] = now
plan = plan.rename(columns={'inter_no':'CRSRD_ID',
                            'start_hour':'HOUR',
                            'start_minute':'MIN',
                            'cycle':'CYCL',
                            'offset':'OFFSET'})
plan = plan.rename(columns={f'dura_{alph}{i}':f'RING{alph}_PHASE{i}' for alph in alphs for i in range(1,9)})
TC_IF_TOD_DAY_PLAN = plan[['CRSRD_ID', 'PLAN_NO', 'HOUR', 'MIN', 'CYCL', 'OFFSET']
                                        + [f'RING{alph}_PHASE{i}' for alph in alphs for i in range(1,9)]
                                        + ['LAST_MDFCN_DT']]
TC_IF_TOD_DAY_PLAN.head()

CRSRD_ID  PLAN_NO  HOUR  MIN  CYCL  OFFSET  RINGA_PHASE1  RINGA_PHASE2  \
0       175        1     0    0   160      57            37            39   
1       175        1     7    0   170      40            40            42   
2       175        1     9    0   180      28            43            45   
3       175        1    18   30   190      18            46            48   
4       176        1     0    0   150     131            37            73   

   RINGA_PHASE3  RINGA_PHASE4  ...  RINGA_PHASE8  RINGB_PHASE1  RINGB_PHASE2  \
0            55            29  ...             0            37            39   
1            55            33  ...             0            40            42   
2            55            37  ...             0            43            45   
3            55            41  ...             0            46            48   
4            40             0  ...             0            37            73   

   RINGB_PHASE3  RINGB_PHASE4  RINGB_PHASE5  RINGB_PHASE6  RINGB_PHASE7  \
0            25            59             0             0             0   
1            29            59             0             0             0   
2            33            59             0             0             0   
3            37            59             0             0             0   
4            40             0             0             0             0   

   RINGB_PHASE8              LAST_MDFCN_DT  
0             0 2024-07-12 16:50:38.378729  
1             0 2024-07-12 16:50:38.378729  
2             0 2024-07-12 16:50:38.378729  
3             0 2024-07-12 16:50:38.378729  
4             0 2024-07-12 16:50:38.378729  

[5 rows x 23 columns]

In [21]:
holidays = [(1,1), (2,9), (2,10), (2,11), (2,12), (3,1), (4,10), (5,1), (5,5), (5,6), (5,15), (6,6), (8,15), (9, 16), (9,17), (9,18), (10,3), (10,9), (12,25)]
TC_IF_TOD_HOLIDAY_PLAN = []
CRSRD_IDs = sorted(TC_IF_TOD_DAY_PLAN.CRSRD_ID.unique())
for CRSRD_ID in CRSRD_IDs:
    for (MNTH, DAY) in holidays:
        TC_IF_TOD_HOLIDAY_PLAN.append({'CRSRD_ID':CRSRD_ID,'MNTH':MNTH, 'DAY':DAY, 'PLAN_NO':1, 'LAST_MDFCN_DT':now})
TC_IF_TOD_HOLIDAY_PLAN = pd.DataFrame(TC_IF_TOD_HOLIDAY_PLAN)
TC_IF_TOD_HOLIDAY_PLAN.head()

CRSRD_ID  MNTH  DAY  PLAN_NO              LAST_MDFCN_DT
0       175     1    1        1 2024-07-12 16:50:38.378729
1       175     2    9        1 2024-07-12 16:50:38.378729
2       175     2   10        1 2024-07-12 16:50:38.378729
3       175     2   11        1 2024-07-12 16:50:38.378729
4       175     2   12        1 2024-07-12 16:50:38.378729

In [22]:
plan = pd.read_csv(os.path.join(path_tables_draft, 'plan.csv'))
plan = plan.drop(columns=[f'dura_{alph}{i}' for alph in alphs for i in range(1,9)]
                                               +['start_hour', 'start_minute', 'cycle', 'offset'])
TC_IF_TOD_RED_YELLO = []
for row in plan.itertuples():
    for i in range(1,9):
        TC_IF_TOD_RED_YELLO.append({
            'CRSRD_ID': row.inter_no,
            'PLAN_NO': 1,
            'PHASE': i,
            'RINGA_FLOW': -1,
            'RINGA_RED_SEC': getattr(row, f'red_A{i}'),
            'RINGA_YELLO_SEC': getattr(row, f'yellow_A{i}'),
            'RINGA_MIN_SEC': -1,
            'RINGB_FLOW': -1,
            'RINGB_RED_SEC': getattr(row, f'red_B{i}'),
            'RINGB_YELLO_SEC': getattr(row, f'yellow_B{i}'),
            'RINGB_MIN_SEC': -1,
            'LAST_MDFCN_DT':now})
TC_IF_TOD_RED_YELLO = pd.DataFrame(TC_IF_TOD_RED_YELLO)
TC_IF_TOD_RED_YELLO.head()

CRSRD_ID  PLAN_NO  PHASE  RINGA_FLOW  RINGA_RED_SEC  RINGA_YELLO_SEC  \
0       175        1      1          -1              1                4   
1       175        1      2          -1              1                4   
2       175        1      3          -1              1                4   
3       175        1      4          -1              1                4   
4       175        1      5          -1              1                4   

   RINGA_MIN_SEC  RINGB_FLOW  RINGB_RED_SEC  RINGB_YELLO_SEC  RINGB_MIN_SEC  \
0             -1          -1              1                4             -1   
1             -1          -1              1                4             -1   
2             -1          -1              1                4             -1   
3             -1          -1              1                4             -1   
4             -1          -1              1                4             -1   

               LAST_MDFCN_DT  
0 2024-07-12 16:50:38.378729  
1 2024-07-12 16:50:38.378729  
2 2024-07-12 16:50:38.378729  
3 2024-07-12 16:50:38.378729  
4 2024-07-12 16:50:38.378729

In [23]:
TC_IF_TOD_WEEK_PLAN = []

for CRSRD_ID in CRSRD_IDs:
    TC_IF_TOD_WEEK_PLAN.append({
        'CRSRD_ID':CRSRD_ID,
        'SUN_PLAN_NO':1,
        'MON_PLAN_NO':1,
        'TUE_PLAN_NO':1,
        'WED_PLAN_NO':1,
        'THU_PLAN_NO':1,
        'FRI_PLAN_NO':1,
        'SAT_PLAN_NO':1,
        'LAST_MDFCN_DT':now,
        })
TC_IF_TOD_WEEK_PLAN = pd.DataFrame(TC_IF_TOD_WEEK_PLAN)
TC_IF_TOD_WEEK_PLAN.head()

CRSRD_ID  SUN_PLAN_NO  MON_PLAN_NO  TUE_PLAN_NO  WED_PLAN_NO  THU_PLAN_NO  \
0       175            1            1            1            1            1   
1       176            1            1            1            1            1   
2       177            1            1            1            1            1   
3       178            1            1            1            1            1   
4       201            1            1            1            1            1   

   FRI_PLAN_NO  SAT_PLAN_NO              LAST_MDFCN_DT  
0            1            1 2024-07-12 16:50:38.378729  
1            1            1 2024-07-12 16:50:38.378729  
2            1            1 2024-07-12 16:50:38.378729  
3            1            1 2024-07-12 16:50:38.378729  
4            1            1 2024-07-12 16:50:38.378729

In [24]:
TL_IF_SIGL_CYCL = pd.read_csv(os.path.join(path_tables_draft, 'history.csv'))
TL_IF_SIGL_CYCL = TL_IF_SIGL_CYCL.rename(columns={**{'inter_no':'CRSRD_ID', 'end_unix':'PHASE_DT'},
                                                  **{f'dura_{alph}{i}':f'RING{alph}_PHASE{i}' for alph in alphs for i in range(1,9)}})
TL_IF_SIGL_CYCL = TL_IF_SIGL_CYCL[['PHASE_DT', 'CRSRD_ID'] + [f'RING{alph}_PHASE{i}' for alph in alphs for i in range(1,9)]]
TL_IF_SIGL_CYCL['PHASE_DT'] = TL_IF_SIGL_CYCL['PHASE_DT'].apply(lambda x:datetime.fromtimestamp(x))
TL_IF_SIGL_CYCL['LAST_MDFCN_DT'] = now
TL_IF_SIGL_CYCL.head()

PHASE_DT  CRSRD_ID  RINGA_PHASE1  RINGA_PHASE2  RINGA_PHASE3  \
0 2024-01-05 00:01:59       206            33            35            26   
1 2024-01-05 00:02:20       178            38            39            40   
2 2024-01-05 00:02:20       201            24            24            17   
3 2024-01-05 00:02:20       202            39           101             0   
4 2024-01-05 00:02:30       177            36            20            68   

   RINGA_PHASE4  RINGA_PHASE5  RINGA_PHASE6  RINGA_PHASE7  RINGA_PHASE8  \
0            26             0             0             0             0   
1            23             0             0             0             0   
2            58            17             0             0             0   
3             0             0             0             0             0   
4            26             0             0             0             0   

   RINGB_PHASE1  RINGB_PHASE2  RINGB_PHASE3  RINGB_PHASE4  RINGB_PHASE5  \
0            33            35            26            26             0   
1            38            39            40            23             0   
2            24            24            17            58            17   
3            39           101             0             0             0   
4            36            20            68            26             0   

   RINGB_PHASE6  RINGB_PHASE7  RINGB_PHASE8              LAST_MDFCN_DT  
0             0             0             0 2024-07-12 16:50:38.378729  
1             0             0             0 2024-07-12 16:50:38.378729  
2             0             0             0 2024-07-12 16:50:38.378729  
3             0             0             0 2024-07-12 16:50:38.378729  
4             0             0             0 2024-07-12 16:50:38.378729

In [25]:
inter_node = pd.read_csv(os.path.join(path_tables_draft, 'inter_node.csv'))
inter_node

inter_no node_id inter_type
0        175      i0     parent
1        175     u00      child
2        176      i1     parent
3        177      i2     parent
4        177     u20      child
5        178      i3     parent
6        178     u30      child
7        178     u31      child
8        178     u32      child
9        201      i8     parent
10       202      i9     parent
11       206      i7     parent
12       210      i6     parent
13       210     u60      child
14       178     c30      child

In [26]:
inter_nos = sorted(inter_node['inter_no'].unique())
node_ids = list(inter_node['node_id'])
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
inter2nodes = {inter:[key for key, value in node2inter.items() if value == inter] for inter in node2inter.values()}
inter2node = dict(zip(inter_node[inter_node.inter_type=='parent']['inter_no'], inter_node[inter_node.inter_type=='parent']['node_id']))
node2type = dict(zip(inter_node['node_id'], inter_node['inter_type']))
child2parent = dict()
for child_id in list(inter_node[inter_node.inter_type=='child']['node_id'].unique()):
    inter_no = inter_node[inter_node.node_id==child_id].iloc[0].inter_no
    parent_id = inter_node[inter_node.inter_no==inter_no][inter_node[inter_node.inter_no==inter_no].inter_type=='parent'].iloc[0].node_id
    child2parent[child_id] = parent_id
parent2childs = {parent_id:[key for key, value in child2parent.items() if value == parent_id] for parent_id in child2parent.values()}
print(inter_nos)
print(node_ids)
print(node2inter)
print(inter2nodes)
print(inter2node)
print(node2type)
print(child2parent)
print(parent2childs)

[175, 176, 177, 178, 201, 202, 206, 210]
['i0', 'u00', 'i1', 'i2', 'u20', 'i3', 'u30', 'u31', 'u32', 'i8', 'i9', 'i7', 'i6', 'u60', 'c30']
{'i0': 175, 'u00': 175, 'i1': 176, 'i2': 177, 'u20': 177, 'i3': 178, 'u30': 178, 'u31': 178, 'u32': 178, 'i8': 201, 'i9': 202, 'i7': 206, 'i6': 210, 'u60': 210, 'c30': 178}
{175: ['i0', 'u00'], 176: ['i1'], 177: ['i2', 'u20'], 178: ['i3', 'u30', 'u31', 'u32', 'c30'], 201: ['i8'], 202: ['i9'], 206: ['i7'], 210: ['i6', 'u60']}
{175: 'i0', 176: 'i1', 177: 'i2', 178: 'i3', 201: 'i8', 202: 'i9', 206: 'i7', 210: 'i6'}
{'i0': 'parent', 'u00': 'child', 'i1': 'parent', 'i2': 'parent', 'u20': 'child', 'i3': 'parent', 'u30': 'child', 'u31': 'child', 'u32': 'child', 'i8': 'parent', 'i9': 'parent', 'i7': 'parent', 'i6': 'parent', 'u60': 'child', 'c30': 'child'}
{'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'u60': 'i6', 'c30': 'i3'}
{'i0': ['u00'], 'i2': ['u20'], 'i3': ['u30', 'u31', 'u32', 'c30'], 'i6': ['u60']}


In [11]:
inter_info = pd.read_csv(os.path.join(path_tables_draft, 'inter_info.csv'))
inter_info.head()

inter_no      inter_name  inter_lat  inter_lon  group_no  main_phase_no
0       175  한솔삼거리(한솔마을3거리)   37.36857  127.11478         3              2
1       176         느티마을4단지   37.36724  127.11480         3              2
2       177   한솔6단지(정자동사무소)   37.36619  127.11480         3              2
3       178           신기4거리   37.36346  127.11480         3              2
4       201         느티마을4거리   37.36854  127.10984         3              2

In [12]:
inter2name = dict(zip(inter_info['inter_no'], inter_info['inter_name']))
inter2LL = dict(zip(inter_info['inter_no'], zip(inter_info['inter_lat'], inter_info['inter_lon'])))
inter2mp = dict(zip(inter_info['inter_no'], inter_info['main_phase_no']))
print(inter2name)
print(inter2LL)
print(inter2mp)

{175: '한솔삼거리(한솔마을3거리)', 176: '느티마을4단지', 177: '한솔6단지(정자동사무소)', 178: '신기4거리', 201: '느티마을4거리', 202: '느티마을 안촌유치원', 206: '상록마을 321동', 210: '상록4거리(상록마을입구4거리)'}
{175: (37.36857, 127.11478), 176: (37.36724, 127.1148), 177: (37.36619, 127.1148), 178: (37.36346, 127.1148), 201: (37.36854, 127.10984), 202: (37.36855, 127.11241), 206: (37.36483, 127.10981), 210: (37.36347, 127.10982)}
{175: 2, 176: 2, 177: 2, 178: 2, 201: 2, 202: 2, 206: 2, 210: 2}


In [13]:
TM_FA_CRSRD = []
for node_id in node_ids:
    inter_no = node2inter[node_id]
    TM_FA_CRSRD.append({
        'CRSRD_ID':inter_no,
        'CRSRD_NM':inter2name[inter_no],
        'CRSRD_TYPE':0 if node2type[node_id]=='parent' else 1,
        'CTRLER_TYPE':-1,
        'TRFLIG_TYPE':-1,
        'NODE_ID':node_id,
        'LTTD':inter2LL[inter_no][0],
        'LGTD':inter2LL[inter_no][1],
        'PPC_TYPE':-1,
        'MAIN_PHASE':inter2mp[inter_no],
        'LOS_YN':-1,
        'USE_YN':-1,
        'FRST_REG_DT':now,
        'LAST_MDFCN_DT':now,
        'MAIN_CRSRD_ID':inter2node[inter_no],
        'GRP_NO':1
    })
TM_FA_CRSRD = pd.DataFrame(TM_FA_CRSRD)
TM_FA_CRSRD

CRSRD_ID          CRSRD_NM  CRSRD_TYPE  CTRLER_TYPE  TRFLIG_TYPE NODE_ID  \
0        175    한솔삼거리(한솔마을3거리)           0           -1           -1      i0   
1        175    한솔삼거리(한솔마을3거리)           1           -1           -1     u00   
2        176           느티마을4단지           0           -1           -1      i1   
3        177     한솔6단지(정자동사무소)           0           -1           -1      i2   
4        177     한솔6단지(정자동사무소)           1           -1           -1     u20   
5        178             신기4거리           0           -1           -1      i3   
6        178             신기4거리           1           -1           -1     u30   
7        178             신기4거리           1           -1           -1     u31   
8        178             신기4거리           1           -1           -1     u32   
9        201           느티마을4거리           0           -1           -1      i8   
10       202        느티마을 안촌유치원           0           -1           -1      i9   
11       206         상록마을 321동           0           -1           -1      i7   
12       210  상록4거리(상록마을입구4거리)           0           -1           -1      i6   
13       210  상록4거리(상록마을입구4거리)           1           -1           -1     u60   
14       178             신기4거리           1           -1           -1     c30   

        LTTD       LGTD  PPC_TYPE  MAIN_PHASE  LOS_YN  USE_YN  \
0   37.36857  127.11478        -1           2      -1      -1   
1   37.36857  127.11478        -1           2      -1      -1   
2   37.36724  127.11480        -1           2      -1      -1   
3   37.36619  127.11480        -1           2      -1      -1   
4   37.36619  127.11480        -1           2      -1      -1   
5   37.36346  127.11480        -1           2      -1      -1   
6   37.36346  127.11480        -1           2      -1      -1   
7   37.36346  127.11480        -1           2      -1      -1   
8   37.36346  127.11480        -1           2      -1      -1   
9   37.36854  127.10984        -1           2      -1      -1   
10  37.36855  127.11241        -1           2      -1      -1   
11  37.36483  127.10981        -1           2      -1      -1   
12  37.36347  127.10982        -1           2      -1      -1   
13  37.36347  127.10982        -1           2      -1      -1   
14  37.36346  127.11480        -1           2      -1      -1   

                  FRST_REG_DT              LAST_MDFCN_DT MAIN_CRSRD_ID  GRP_NO  
0  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i0       1  
1  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i0       1  
2  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i1       1  
3  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i2       1  
4  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i2       1  
5  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i3       1  
6  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i3       1  
7  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i3       1  
8  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i3       1  
9  2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i8       1  
10 2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i9       1  
11 2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i7       1  
12 2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i6       1  
13 2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i6       1  
14 2024-07-12 16:36:43.702267 2024-07-12 16:36:43.702267            i3       1

In [14]:
print(os.path.join(path_tables_draft, 'angle_old.csv'))

c:\Github\snits_siggen\draft\data\tables\angle_old.csv


In [15]:
angle = pd.read_csv(os.path.join(path_tables_draft, 'angle_old.csv'), dtype={f'angle_{alph}{i}':str for alph in alphs for i in range(1,9)}, index_col=0)

TN_IF_SIGL_FLOW = []
for row in angle.itertuples():
    inter_no = row.inter_no
    for i in range(1,9):
        for alph in alphs:
            TN_IF_SIGL_FLOW.append({
                'CRSRD_ID':inter_no,
                'PHASE':i,
                'RING':alph,
                'FLOW_NO':-1,
                'STOS_NO':0,
                'SIGL_ANGLE':getattr(row, f'angle_{alph}{i}')
            })
TN_IF_SIGL_FLOW = pd.DataFrame(TN_IF_SIGL_FLOW)
TN_IF_SIGL_FLOW

CRSRD_ID  PHASE RING  FLOW_NO  STOS_NO SIGL_ANGLE
0         175      1    A       -1        0     179004
1         175      1    B       -1        0     003176
2         175      2    A       -1        0     001095
3         175      2    B       -1        0     179271
4         175      3    A       -1        0     092270
..        ...    ...  ...      ...      ...        ...
123       210      6    B       -1        0        NaN
124       210      7    A       -1        0        NaN
125       210      7    B       -1        0        NaN
126       210      8    A       -1        0        NaN
127       210      8    B       -1        0        NaN

[128 rows x 6 columns]

In [16]:
TC_IF_TOD_DAY_PLAN.to_csv(os.path.join(path_tables, 'TC_IF_TOD_DAY_PLAN.csv'), index=0)
TC_IF_TOD_HOLIDAY_PLAN.to_csv(os.path.join(path_tables, 'TC_IF_TOD_HOLIDAY_PLAN.csv'), index=0)
TC_IF_TOD_RED_YELLO.to_csv(os.path.join(path_tables, 'TC_IF_TOD_RED_YELLO.csv'), index=0)
TC_IF_TOD_WEEK_PLAN.to_csv(os.path.join(path_tables, 'TC_IF_TOD_WEEK_PLAN.csv'), index=0)
TL_IF_SIGL_CYCL.to_csv(os.path.join(path_tables, 'TL_IF_SIGL_CYCL.csv'), index=0)
TM_FA_CRSRD.to_csv(os.path.join(path_tables, 'TM_FA_CRSRD.csv'), index=0)
TN_IF_SIGL_FLOW.to_csv(os.path.join(path_tables, 'TN_IF_SIGL_FLOW.csv'), index=0)